# DDI-ML. Relation Extraction

Setup
cd into ../stanford-corenlp-4.2.0 and run

`java -mx4g -cp "*" edu.stanford.nlp.pipeline.StanfordCoreNLPServer`

In [1]:
from os import listdir
from xml.dom.minidom import parse
import networkx
# import nltk CoreNLP module (just once)
from nltk.parse.corenlp import CoreNLPDependencyParser
# connect to your CoreNLP server (just once)
corenlp_parser = CoreNLPDependencyParser(url="http://localhost:9000")

from evaluator import *

## Feature Extractor

In [2]:
def get_offsets(word, s):
    '''
    Task:
        Given a word and sentence, returns its starting end ending index in the sentence.
    
    Input:
        word: word to find offsets for
        s: sentence containing the word
    
    Output:
        Returns a tuple containing the start and end offset.
    '''
    start = s.find(word)
    end = start + len(word) - 1
    return start, end

In [3]:
def preprocess(s):
    '''
    Task:
        Helper function
    '''
    # because otherwise CoreNLP throws 500
    return s.replace("%", "<percentage>")

In [4]:
def analyze(s):
    '''
    Task:
        Given one sentence, sends it to CoreNLP to obtain the tokens, tags,
        and dependency tree. It also adds the start/end offsets to each token.
    
    Input:
        s: string containing the text for one sentence
    
    Output:
        Returns the nltk DependencyGraph object produced by CoreNLP, enriched with token  offsets.

    '''
    s = s.replace("%", "<percentage>")
    tree, = corenlp_parser.raw_parse(s)
    for n in tree.nodes.items():
        node = n[1]
        if node['word']:
            start, end = get_offsets(node['word'], s)
            node['start'] = start
            node['end'] = end
            
    return tree

In [8]:
def find_entity_in_tree(eid, entities, tree):
    start_e1 = entities[eid][0]
    end_e1 = entities[eid][1]
    
    for n in tree.nodes.items():
        node = n[1]
        if node['word'] and node['start'] == int(start_e1): # and node['end'] == int(end_e1)):
            return node
    
    # TODO: handle two-word entities like "beta-endorphin"
    # We can extract here word, lemma, tag

In [9]:
def find_head(tree, entity):
    for n in tree.nodes.items():
            node = n[1]
            if  node['address'] == entity['head']:
                return node
    # We can extract here word, lemma, tag

In [10]:
def traverse_path(path, tree):
    if len(path) == 0:
        return None
    path_nodes = [tree.nodes[x] for x in path]
    str_path = ""
    # traverse from e1 up
    current_node = path_nodes[0]
    while (current_node['head'] in path):
        
        rel = current_node['rel']
        current_node = tree.nodes[current_node['head']]
        str_path += (rel + '<')
    
    str_path += current_node['lemma'] 
    # traverse from e2 up
    current_node = path_nodes[-1]
    while(current_node['head'] in path):
        rel = current_node['rel']
        current_node = tree.nodes[current_node['head']]
        str_path += ('>' + rel)
        
    return str_path
    

In [11]:
CLUE_VERBS = ['administer', 'enhance', 'interact', 'coadminister', 'increase', 'decrease'] # add more?
NEGATIVE_WORDS = ['No', 'not', 'neither', 'without', 'lack', 'fail', 'unable', 'abrogate',
                  'absence', 'prevent','unlikely', 'unchanged', 'rarely']

def find_clue_verbs(path, tree):
    path_nodes = [tree.nodes[x]['lemma'] for x in path]
    feats = []
    for pn in path_nodes:
        if pn in CLUE_VERBS:
            feats.append('lemmainbetween=%s' % pn)
            
    return feats

def negative_words_path(path, tree):
    path_nodes = [tree.nodes[x]['word'] for x in path]
    count = 0
    for pn in path_nodes:
        if pn in NEGATIVE_WORDS or pn[-3:] == "n't":
            count += 1
    return count

def negative_words_sentence(tree):
    count = 0
    for n in tree.nodes.items():
        word = n[1]['word']
        if word in NEGATIVE_WORDS:
            count += 1
    return count

In [12]:
def extract_features(tree, entities, e1, e2) :
    '''
    Task:
        Given an analyzed sentence and two target entities , compute a feature
        vector for this classification example .
    Input:
        tree: a DependencyGraph object with all sentence information .
        entities: A list of all entities in the sentence (id and offsets).
        e1, e2: ids of the two entities to be checked for an interaction
    Output:
        A vector of binary features .
        Features are binary and vectors are in sparse representation (i.e. only
        active features are listed)
   '''
    int_verbs = ['interact', 'interaction']
    mech_verbs = ['metabolism', 'concentration', 'clearance', 'level', 'absorption', 'dose',
                 'presence', 'interfere']
    adv_verbs = ['co-administration', 'take', 'coadminister', 'treatment', 'therapy', 'tell']
    eff_verbs = ['effect', 'alcohol', 'action','use', 'combination', 'inhibitor',
                'response', 'effect', 'enhance', 'diminish']
      
    e1_node = find_entity_in_tree(e1, entities, tree)
    e2_node = find_entity_in_tree(e2, entities, tree)
    
    e1_head = find_head(tree, e1_node) if e1_node else None
    e2_head = find_head(tree, e2_node) if e2_node else None
    
    h1_lemma = e1_head['lemma'] if e1_node else None
    h2_lemma = e2_head['lemma'] if e2_node else None
    
    tag_head_e1 = e1_head['tag'] if e1_head else None
    tag_head_e2 = e2_head['tag'] if e2_head else None
    
    nxgraph = tree.nx_graph().to_undirected()
    shortest_path = networkx.shortest_path(nxgraph, e1_node['address'], e2_node['address']) if (e1_node and e2_node) else []
    path = traverse_path(shortest_path, analysis)
    find_clue_verbs(shortest_path, analysis)
    count_neg_p = negative_words_path(shortest_path, analysis)
    count_neg_s = negative_words_sentence(tree)

    
    # --- FEATURES ---
    features = ['h1_lemma=%s' %h1_lemma,
                'h2_lemma=%s' %h2_lemma,
                'h1_tag=%s' %tag_head_e1,
                'h2_tag=%s' %tag_head_e2,
                'path=%s' % path,
                'neg_words_p=%s' %count_neg_p,  # only 28 with 1, 1 with 2
                'neg_words_s=%s' %count_neg_s   # 3144 with 1, 270 with 2, 4 with 3 
                ] + find_clue_verbs(shortest_path, analysis)
    
    
    if (e1_head and e2_head):
        if h1_lemma == h2_lemma:  # should use address? 
            features.append('under_same=True') # 5609 occurrences
            if tag_head_e1[0].lower() == 'v':
                features.append('under_same_verb=True') # 173 occurrences
            else:
                features.append('under_same_verb=False')
        else:
            features.append('under_same=False')
            features.append('under_same_verb=False')
            
        if h1_lemma == e2_node['lemma']:
            features.append('1under2=True') # 136 occ
        else:
            features.append('1under2=False')
            
        if h2_lemma == e1_node['lemma']:
            features.append('2under1=True') # 1953 occ
        else:
            features.append('2under1=False')
        
        if h1_lemma in int_verbs or h2_lemma in int_verbs:
            features.append('intVerbs=True') # 458
        else:
            features.append('intVerbs=False')
            
        if h1_lemma in mech_verbs or h2_lemma in mech_verbs:
            features.append('mechVerbs=True') # 1030
        else:
            features.append('mechVerbs=False')

        if h1_lemma in adv_verbs or h2_lemma in adv_verbs:
            features.append('advVerbs=True') # 569
        else:
            features.append('advVerbs=False')

        if h1_lemma in eff_verbs or h2_lemma in eff_verbs:
            features.append('effVerbs=True') # 3480
        else:
            features.append('effVerbs=False')
        
    else:
        None
        
    # Distance between entities 
    # Type of entities (drug, brand, group) in the pair
        
    return features

In [13]:
datadir = "../../labAHLT/data/train"

outfile = "devel_feats.dat"

# process each file in directory
for f in listdir(datadir):
    # parse XML file , obtaining a DOM tree
    tree = parse(datadir + "/" + f)
    # process each sentence in the file
    sentences = tree.getElementsByTagName("sentence")
    for s in sentences:

        sid = s.attributes["id"].value # get sentence id
        stext = s.attributes["text"].value # get sentence text
        
        # CoreNLP throws error for empty sentences
        if len(stext) == 0:
            continue

        # load sentence ground truth entities
        entities = {}
        ents = s.getElementsByTagName("entity")
        for e in ents:
            eid = e . attributes["id"].value
            entities[eid] = e.attributes["charOffset"].value.split("-")

        # analyze sentence if there is at least a pair of entities
        if len(entities) > 1: analysis = analyze(stext)

        # for each pair in the sentence , decide whether it is DDI and its type
        pairs = s.getElementsByTagName("pair")
        for p in pairs:
            # get ground truth
            ddi = p.attributes["ddi"].value
            dditype = p.attributes["type"].value if ddi == "true" else "null"
            
            # target entities
            id_e1 = p.attributes["e1"].value
            id_e2 = p.attributes["e2"].value
            
            # feature extraction
            feats = extract_features(analysis, entities, id_e1, id_e2)
            
            # resulting feature vector
            print(sid, id_e1, id_e2, dditype, "|".join(feats), sep="|") 
            

DDI-DrugBank.d59.s0|DDI-DrugBank.d59.s0.e0|DDI-DrugBank.d59.s0.e1|mechanism|h1_lemma=effect|h2_lemma=potentiate|h1_tag=NNS|h2_tag=VBN|path=nmod<nsubj:pass<potentiate>obl|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=True
DDI-DrugBank.d59.s0|DDI-DrugBank.d59.s0.e0|DDI-DrugBank.d59.s0.e2|null|h1_lemma=effect|h2_lemma=metabolism|h1_tag=NNS|h2_tag=NN|path=nmod<nsubj:pass<potentiate>nmod>obj>ccomp|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=True|advVerbs=False|effVerbs=True
DDI-DrugBank.d59.s0|DDI-DrugBank.d59.s0.e1|DDI-DrugBank.d59.s0.e2|mechanism|h1_lemma=potentiate|h2_lemma=metabolism|h1_tag=VBN|h2_tag=NN|path=obl<potentiate>nmod>obj>ccomp|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=True|advVerbs=False|effVerbs=False
DDI-DrugBank.d59.s1

DDI-DrugBank.d335.s5|DDI-DrugBank.d335.s5.e0|DDI-DrugBank.d335.s5.e1|null|h1_lemma=administration|h2_lemma=tablet|h1_tag=NN|h2_tag=NNS|path=nmod<nsubj<influence>compound>nmod>obj|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d150.s0|DDI-DrugBank.d150.s0.e0|DDI-DrugBank.d150.s0.e1|int|h1_lemma=have|h2_lemma=inhibitor|h1_tag=VB|h2_tag=NNS|path=nsubj<have>compound>nmod>obj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=True
DDI-DrugBank.d150.s1|DDI-DrugBank.d150.s1.e0|DDI-DrugBank.d150.s1.e1|effect|h1_lemma=enhance|h2_lemma=effect|h1_tag=VB|h2_tag=NNS|path=nsubj<enhance>nmod>obj|neg_words_p=0|neg_words_s=0|lemmainbetween=enhance|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=True
DDI-DrugBank.

DDI-DrugBank.d491.s1|DDI-DrugBank.d491.s1.e0|DDI-DrugBank.d491.s1.e1|null|h1_lemma=treatment|h2_lemma=therapy|h1_tag=NN|h2_tag=NN|path=nmod<nmod<nsubj<consider>amod>obj>csubj:pass>xcomp|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=True|effVerbs=False
DDI-DrugBank.d491.s16|DDI-DrugBank.d491.s16.e0|DDI-DrugBank.d491.s16.e1|null|h1_lemma=effect|h2_lemma=None|h1_tag=NN|h2_tag=None|path=None|neg_words_p=0|neg_words_s=1
DDI-DrugBank.d491.s16|DDI-DrugBank.d491.s16.e0|DDI-DrugBank.d491.s16.e2|null|h1_lemma=effect|h2_lemma=None|h1_tag=NN|h2_tag=None|path=None|neg_words_p=0|neg_words_s=1
DDI-DrugBank.d491.s16|DDI-DrugBank.d491.s16.e1|DDI-DrugBank.d491.s16.e2|null|h1_lemma=None|h2_lemma=None|h1_tag=None|h2_tag=None|path=None|neg_words_p=0|neg_words_s=1
DDI-DrugBank.d726.s1|DDI-DrugBank.d726.s1.e0|DDI-DrugBank.d726.s1.e1|mechanism|h1_lemma=double|h2_lemma=auc0|h1_tag=VBD|h2_tag=NN|path=nsubj<double>compound>n

DDI-DrugBank.d193.s0|DDI-DrugBank.d193.s0.e0|DDI-DrugBank.d193.s0.e1|null|h1_lemma=administer|h2_lemma=administer|h1_tag=VBN|h2_tag=VBN|path=nsubj:pass<administer>obl|neg_words_p=0|neg_words_s=0|lemmainbetween=administer|under_same=True|under_same_verb=True|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d193.s1|DDI-DrugBank.d193.s1.e0|DDI-DrugBank.d193.s1.e1|null|h1_lemma=interaction|h2_lemma=ERBITUX|h1_tag=NNS|h2_tag=NNP|path=ERBITUX>conj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=True|intVerbs=True|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d216.s0|DDI-DrugBank.d216.s0.e0|DDI-DrugBank.d216.s0.e1|null|h1_lemma=cns|h2_lemma=coadministration|h1_tag=NN|h2_tag=NN|path=dep<nsubj:pass<see>nmod>obl|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d216.s0|DDI-

DDI-DrugBank.d216.s15|DDI-DrugBank.d216.s15.e0|DDI-DrugBank.d216.s15.e1|null|h1_lemma=A|h2_lemma=dose|h1_tag=NNP|h2_tag=NN|path=compound<compound<dose>nmod|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=True|advVerbs=False|effVerbs=False
DDI-DrugBank.d216.s15|DDI-DrugBank.d216.s15.e0|DDI-DrugBank.d216.s15.e2|null|h1_lemma=A|h2_lemma=pharmacokinetic|h1_tag=NNP|h2_tag=NNS|path=compound<compound<obl<affect>nmod>obj|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d216.s15|DDI-DrugBank.d216.s15.e1|DDI-DrugBank.d216.s15.e2|null|h1_lemma=dose|h2_lemma=pharmacokinetic|h1_tag=NN|h2_tag=NNS|path=nmod<obl<affect>nmod>obj|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=True|advVerbs=False|effVerbs=False
DDI-DrugBank.d216.s16|DDI-DrugBan

...

DDI-MedLine.d200.s0|DDI-MedLine.d200.s0.e0|DDI-MedLine.d200.s0.e1|null|h1_lemma=valsartan|h2_lemma=efficacy|h1_tag=NN|h2_tag=NN|path=compound<valsartan|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=True|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-MedLine.d200.s1|DDI-MedLine.d200.s1.e0|DDI-MedLine.d200.s1.e1|null|h1_lemma=valsartan|h2_lemma=combination|h1_tag=NN|h2_tag=NN|path=compound<valsartan|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=True|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=True
DDI-MedLine.d200.s2|DDI-MedLine.d200.s2.e0|DDI-MedLine.d200.s2.e1|null|h1_lemma=valsartan|h2_lemma=randomize|h1_tag=NN|h2_tag=VBN|path=compound<valsartan|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=True|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-MedLine.d200.s7|DDI-MedLine.d200.s7.e0|DDI-MedLine.d200.s7.e1|null|h1_l

DDI-DrugBank.d543.s4|DDI-DrugBank.d543.s4.e0|DDI-DrugBank.d543.s4.e1|mechanism|h1_lemma=agent|h2_lemma=form|h1_tag=NNS|h2_tag=NNS|path=amod<nsubj<affect>nmod>nmod>nmod>obj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d543.s6|DDI-DrugBank.d543.s6.e0|DDI-DrugBank.d543.s6.e1|mechanism|h1_lemma=drug|h2_lemma=motility|h1_tag=NNS|h2_tag=NN|path=amod<nsubj<antagonize>nmod>obj>acl:relcl>obj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d543.s7|DDI-DrugBank.d543.s7.e0|DDI-DrugBank.d543.s7.e1|mechanism|h1_lemma=interfere|h2_lemma=agent|h1_tag=VB|h2_tag=NNS|path=nsubj<interfere>amod>nmod>obl|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=True|advVerbs=False|effVerbs=False
DDI-DrugBa

DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e1|null|h1_lemma=None|h2_lemma=None|h1_tag=None|h2_tag=None|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e2|null|h1_lemma=None|h2_lemma=None|h1_tag=None|h2_tag=None|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e3|null|h1_lemma=None|h2_lemma=acid|h1_tag=None|h2_tag=NN|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e4|null|h1_lemma=None|h2_lemma=None|h1_tag=None|h2_tag=None|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e5|null|h1_lemma=None|h2_lemma=acid|h1_tag=None|h2_tag=NN|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4|DDI-DrugBank.d627.s4.e0|DDI-DrugBank.d627.s4.e6|null|h1_lemma=None|h2_lemma=None|h1_tag=None|h2_tag=None|path=None|neg_words_p=0|neg_words_s=0
DDI-DrugBank.d627.s4

DDI-DrugBank.d353.s2|DDI-DrugBank.d353.s2.e0|DDI-DrugBank.d353.s2.e1|null|h1_lemma=absence|h2_lemma=effect|h1_tag=NN|h2_tag=NN|path=nmod<nmod<obj<nsubj<detect>nmod>obj|neg_words_p=1|neg_words_s=2|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advVerbs=False|effVerbs=True
DDI-DrugBank.d353.s4|DDI-DrugBank.d353.s4.e0|DDI-DrugBank.d353.s4.e1|null|h1_lemma=contraceptive|h2_lemma=interaction|h1_tag=NNS|h2_tag=NN|path=amod<contraceptive>nmod>nsubj>advcl>parataxis|neg_words_p=0|neg_words_s=1|under_same=False|under_same_verb=False|1under2=False|2under1=False|intVerbs=True|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d353.s4|DDI-DrugBank.d353.s4.e0|DDI-DrugBank.d353.s4.e2|null|h1_lemma=contraceptive|h2_lemma=contraceptive|h1_tag=NNS|h2_tag=NNS|path=amod<contraceptive>amod>conj>nmod>nsubj>advcl>parataxis|neg_words_p=0|neg_words_s=1|under_same=True|under_same_verb=False|1under2=False|2under1=False|intVerbs=False|mechVerbs=False|advV

DDI-DrugBank.d353.s13|DDI-DrugBank.d353.s13.e0|DDI-DrugBank.d353.s13.e1|null|h1_lemma=interaction|h2_lemma=acitretin|h1_tag=NN|h2_tag=NN|path=acitretin>conj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=True|intVerbs=True|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d353.s13|DDI-DrugBank.d353.s13.e0|DDI-DrugBank.d353.s13.e2|null|h1_lemma=interaction|h2_lemma=acitretin|h1_tag=NN|h2_tag=NN|path=acitretin>conj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=True|intVerbs=True|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d353.s13|DDI-DrugBank.d353.s13.e0|DDI-DrugBank.d353.s13.e3|null|h1_lemma=interaction|h2_lemma=acitretin|h1_tag=NN|h2_tag=NN|path=acitretin>conj|neg_words_p=0|neg_words_s=0|under_same=False|under_same_verb=False|1under2=False|2under1=True|intVerbs=True|mechVerbs=False|advVerbs=False|effVerbs=False
DDI-DrugBank.d353.s13|DDI-DrugBank.d353.s13.e1|DDI-DrugBank.d353.s1

## Learner

In [14]:
from itertools import groupby

In [15]:
def parse_string(line):
    split_data = line[:-1].split('|')
    print(split_data)
    sentence_id = split_data[0]
    e1_id = split_data[1]
    e2_id = split_data[2]
    interaction = split_data[3]
    features = split_data[4:]
    return e1_id, e2_id, features, interaction

In [16]:
def read_feature_file(filepath):
    
    f = open(filepath, 'r')
    lines = f.readlines()

    data = []

    for line in lines:
        e1, e2, features, interaction = parse_string(line)
        data.append((features, interaction))
    return data

In [62]:
#read_feature_file("./train_feats.txt")